#### Dependencies

In [119]:
#!pip install numpy pandas requests scipy pydendroheatmap matplotlib
import pandas as pd
import numpy as np
import requests
from collections import defaultdict
import json
import matplotlib
import pydendroheatmap as pdh
import scipy.cluster.hierarchy as sch
import scipy.spatial.distance as ssd

#### Config

In [120]:
awatch = {'polls': "https://www.abgeordnetenwatch.de/api/v2/polls?field_legislature=%(legislature)d&range_start=%(range_start)d&range_end=%(range_end)d",
         'votes': "https://www.abgeordnetenwatch.de/api/v2/votes?poll=%(poll)d&range_start=%(range_start)d&range_end=%(range_end)d",
        }

legis_id = 111  # id of contemporary legislature period

#matplotlib.rcParams['figure.dpi'] = 300
#matplotlib.rcParams['figure.figsize'] = (16,9)

g_votes = {}

#### Functions

In [193]:
def from_url(url, max_range=float("inf"), **kw):
    result = []
    
    meta={'total': max_range, 'range_end': -1}
    
    while min(meta['total'], max_range) > meta['range_end']:
        kw.update({'range_start': meta['range_end']+1, 
                   'range_end': min(max_range, meta['total'], meta['range_end']+101)})
        
        page = requests.get(url % kw).json()
        result.extend(page['data'])
        
        meta = page['meta']['result']
        print("dl: %s %02.0d%%" % (url % kw, 100 * meta['range_end'] / meta['total']))
    return result

def yesno(_polls, max_polls=float("inf")):
    global g_votes
    _votes = defaultdict(lambda: defaultdict(int))
    _absent = defaultdict(lambda: defaultdict(int))
    _mandates = set()
    
    for ipoll, poll in enumerate(_polls):
        if ipoll >= max_polls:
            break

        if poll['id'] not in g_votes:
            g_votes[poll['id']] = from_url(awatch['votes'], poll=poll['id'])

        for vote in g_votes[poll['id']]:
            mandate = vote['mandate']['label']
            mandate += " (" + (vote['fraction']['label'] if vote['fraction'] else "?") + ")"
            mandate = mandate.replace(" (Bundestag 2017 - 2021)", '')
            _mandates.add(mandate)
            
            if vote['vote'] in "yes,no":
                _votes[poll['label']][mandate] = 1 if vote['vote'] == "yes" else -1
            if vote['vote'] in "no_show,abstain":
                _absent[poll['label']][mandate] = 1 if vote['vote'] == "abstain" else -1
    
    _mandates = sorted(list(_mandates))
    return pd.DataFrame(data={p: [_votes[p][m] for m in _mandates] for p in _votes}, index=_mandates, dtype=float), \
           pd.DataFrame(data={p: [_absent[p][m] for m in _mandates] for p in _absent}, index=_mandates, dtype=float)

#### Receive serious data

In [158]:
polls = from_url(awatch['polls'], legislature=legis_id)

dl: https://www.abgeordnetenwatch.de/api/v2/polls?field_legislature=111&range_start=0&range_end=100 57%
dl: https://www.abgeordnetenwatch.de/api/v2/polls?field_legislature=111&range_start=101&range_end=175 100%


In [194]:
_yesno, _absent = yesno(polls)
display(_yesno)

Fortbestand der epidemischen Lage von nationaler Tragweite  \
Achim Kessler (DIE LINKE)                                                    -1.0            
Achim Post (SPD)                                                              1.0            
Agnieszka Brugger (DIE GRÜNEN)                                               -1.0            
Albert Rupprecht (CDU/CSU)                                                   -1.0            
Albert Stegemann (CDU/CSU)                                                    1.0            
...                                                                           ...            
Wolfgang Wiehle (AfD)                                                        -1.0            
Yasmin Fahimi (SPD)                                                           1.0            
Yvonne Magwas (CDU/CSU)                                                       1.0            
Zaklin Nastic (DIE LINKE)                                                    -1.0            
Zeki Gökhan (DIE LINKE)                                                      -1.0            

                                Einsatz deutscher Streitkräfte zur militärischen Evakuierung aus Afghanistan  \
Achim Kessler (DIE LINKE)                                                     0.0                              
Achim Post (SPD)                                                              1.0                              
Agnieszka Brugger (DIE GRÜNEN)                                                1.0                              
Albert Rupprecht (CDU/CSU)                                                    1.0                              
Albert Stegemann (CDU/CSU)                                                    1.0                              
...                                                                           ...                              
Wolfgang Wiehle (AfD)                                                         0.0                              
Yasmin Fahimi (SPD)                                                           1.0                              
Yvonne Magwas (CDU/CSU)                                                       1.0                              
Zaklin Nastic (DIE LINKE)                                                    -1.0                              
Zeki Gökhan (DIE LINKE)                                                      -1.0                              

                                Änderung im Infektions­schutz­gesetz  \
Achim Kessler (DIE LINKE)                                        0.0   
Achim Post (SPD)                                                 1.0   
Agnieszka Brugger (DIE GRÜNEN)                                   1.0   
Albert Rupprecht (CDU/CSU)                                       1.0   
Albert Stegemann (CDU/CSU)                                       1.0   
...                                                              ...   
Wolfgang Wiehle (AfD)                                           -1.0   
Yasmin Fahimi (SPD)                                              1.0   
Yvonne Magwas (CDU/CSU)                                          0.0   
Zaklin Nastic (DIE LINKE)                                       -1.0   
Zeki Gökhan (DIE LINKE)                                          0.0   

                                Keine Verwendung von geschlechtergerechter Sprache  \
Achim Kessler (DIE LINKE)                                                     0.0    
Achim Post (SPD)                                                             -1.0    
Agnieszka Brugger (DIE GRÜNEN)                                               -1.0    
Albert Rupprecht (CDU/CSU)                                                   -1.0    
Albert Stegemann (CDU/CSU)                                                   -1.0    
...                                                                           ...    
Wolfgang Wiehle (AfD)                                                         1.0    
Yasmi

#### Render a dendroheatmap of all votes of all mandates and all polls (Bundestag 2017-2021)

In [204]:
#!pip install seaborn fastcluster

import seaborn

g = seaborn.clustermap(data=_yesno*-1,
                       figsize=(50,300),
                       tree_kws=dict(linewidths=2.5),
                       cmap='coolwarm',
                       center=0,
                       cbar_pos=None,
                       facecolor='w')
g.savefig("blau-pro--rot-contra.jpg")
g

In [205]:
g = seaborn.clustermap(data=_absent*-1,
                       figsize=(50,300),
                       tree_kws=dict(linewidths=2.5),
                       cmap='coolwarm',
                       center=0,
                       cbar_pos=None,
                       facecolor='w')
g.savefig("blau-enthaltung--rot-abwesend.jpg")
g